##Import Libraries

In [0]:
from pyspark.sql import SparkSession, Window
from datetime import datetime
from pyspark.sql.functions import explode, col, lit, when, to_date, trim, arrays_zip, split, lower, round, explode_outer, regexp_replace, max, coalesce, regexp_extract, substring, instr, length
import builtins
from pyspark.sql.types import *

In [0]:
# mount data
mount_point = "/mnt/adverse-events"

In [0]:
# unmount if needed
mount_point = mount_point
dbutils.fs.unmount(mount_point)

/mnt/adverse-events has been unmounted.


True

##Connect to Storage Account

In [0]:
# connect to storage account and containers
configs = {"fs.azure.account.auth.type": "OAuth",
           "fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
           "fs.azure.account.oauth2.client.id": "e99fd849-a6b3-49c5-b7a0-044016a9b700",
           "fs.azure.account.oauth2.client.secret": dbutils.secrets.get(scope = "key-vault-scope", key = "client-secret") ,
           "fs.azure.account.oauth2.client.endpoint": "https://login.microsoftonline.com/62a42a60-1f3b-41ee-92d8-d46ce7b9d9ef/oauth2/token/"}

# mount data
dbutils.fs.mount(
    source = "abfss://adverse-events@adverseeventsa.dfs.core.windows.net",
    mount_point = mount_point,
    extra_configs = configs
)

True

In [0]:
%fs
ls "/mnt/adverse-events"

path name size modificationTime dbfs:/mnt/adverse-events/raw-data/ raw-data/ 0 1728067477000 dbfs:/mnt/adverse-events/transformed-data/ transformed-data/ 0 1728067489000

##Read JSON into a Spark DataFrame

In [0]:
directory_path = "dbfs:/mnt/adverse-events/raw-data/"
files = dbutils.fs.ls(directory_path)
print(files)
print()

# use builtin max function - not spark max
latest_file = builtins.max(files, key=lambda x: x.modificationTime).path
print(latest_file)

spark = SparkSession.builder.appName("JSON Parser").getOrCreate()

latest_file = 'dbfs:/mnt/adverse-events/raw-data/fda_adverse_events_extract_2024-01-01-TO-2024-12-31.json'
df = spark.read.json(latest_file)

exploded_df = df.withColumn("results", explode(col("results"))) 


[FileInfo(path='dbfs:/mnt/adverse-events/raw-data/fda_adverse_events_extract_2015-01-01-TO-2015-12-31.json', name='fda_adverse_events_extract_2015-01-01-TO-2015-12-31.json', size=14485018982, modificationTime=1730140145000), FileInfo(path='dbfs:/mnt/adverse-events/raw-data/fda_adverse_events_extract_2016-01-01-TO-2016-12-31.json', name='fda_adverse_events_extract_2016-01-01-TO-2016-12-31.json', size=16645598394, modificationTime=1730135156000), FileInfo(path='dbfs:/mnt/adverse-events/raw-data/fda_adverse_events_extract_2017-01-01-TO-2017-12-31.json', name='fda_adverse_events_extract_2017-01-01-TO-2017-12-31.json', size=17408305231, modificationTime=1730129494000), FileInfo(path='dbfs:/mnt/adverse-events/raw-data/fda_adverse_events_extract_2018-01-01-TO-2018-12-31.json', name='fda_adverse_events_extract_2018-01-01-TO-2018-12-31.json', size=21625503696, modificationTime=1730081327000), FileInfo(path='dbfs:/mnt/adverse-events/raw-data/fda_adverse_events_extract_2019-01-01-TO-2019-12-31.js

##Parse Patient Data into Spark DataFrame for Patient Dimension Table

In [0]:
# Select key fields for viewing
dim_patient = exploded_df.select(
    col("results.safetyreportid").alias("patient_id"),
    col("results.patient.patientonsetage").alias("patient_onset_age"),
    col("results.patient.patientonsetageunit").alias("patient_onset_age_unit"),
    col("results.patient.patientagegroup").alias("patient_age_group"),
    col("results.patient.patientsex").alias("patient_sex"),
    col("results.patient.patientweight").alias("patient_weight(kg)")
)

# convert onset age to interger and calculate to years
dim_patient = dim_patient.withColumn("patient_onset_age", col("patient_onset_age").cast(IntegerType()))

dim_patient = dim_patient.withColumn("patient_onset_age", 
                                     when(dim_patient.patient_onset_age_unit == 800, dim_patient.patient_onset_age*10)
                                     .when(dim_patient.patient_onset_age_unit == 802, dim_patient.patient_onset_age/12)
                                     .when(dim_patient.patient_onset_age_unit == 803, dim_patient.patient_onset_age/52)
                                     .when(dim_patient.patient_onset_age_unit == 803, dim_patient.patient_onset_age/365)
                                     .when(dim_patient.patient_onset_age_unit == 804, dim_patient.patient_onset_age/8760)
                                     .otherwise(dim_patient.patient_onset_age))
# round age (years) to two decimals                                    
dim_patient = dim_patient.withColumn("patient_onset_age", round(col("patient_onset_age"), 2))

# when onset age is give but age group is not given, calculate age group
dim_patient = dim_patient.withColumn("patient_age_group", 
                                     when(dim_patient.patient_onset_age < 0.2, 'Neonate')
                                     .when(dim_patient.patient_onset_age < 1, 'Infant')
                                     .when(dim_patient.patient_onset_age < 12, 'Child')
                                     .when(dim_patient.patient_onset_age < 19, 'Adolescent')
                                     .when(dim_patient.patient_onset_age < 66, 'Adult')
                                     .when(dim_patient.patient_onset_age > 65, 'Elderly')
                                     .otherwise(when(dim_patient.patient_age_group == '1', 'Neonate')
                                               .when(dim_patient.patient_age_group == '2', 'Infant')
                                               .when(dim_patient.patient_age_group == '3', 'Child')
                                               .when(dim_patient.patient_age_group == '4', 'Adolescent')
                                               .when(dim_patient.patient_age_group == '5', 'Adult')
                                               .when(dim_patient.patient_age_group == '6', 'Elderly')))

dim_patient = dim_patient.withColumn("patient_sex", 
                                     when(dim_patient.patient_sex == 1, 'Male')
                                     .when(dim_patient.patient_sex == 2, 'Female')
                                     .otherwise("Unknown"))
dim_patient = dim_patient.filter('patient_onset_age <= 120')
dim_patient = dim_patient.drop(col('patient_onset_age_unit'))
dim_patient = dim_patient.dropna(subset=['patient_onset_age'])
dim_patient = dim_patient.withColumn('patient_id', col('patient_id').cast(IntegerType()))
display(dim_patient)

patient_id patient_onset_age patient_age_group patient_sex patient_weight(kg) 23353582 50.0 Adult Female null 23353583 89.0 Elderly Male null 23353586 54.0 Adult Male null 23353588 61.0 Adult Male null 23353589 57.0 Adult Female null 23353590 60.0 Adult Female null 23353591 83.0 Elderly Male null 23353592 62.0 Adult Female null 23353593 84.0 Elderly Female null 23353595 53.0 Adult Male 82 23353596 31.0 Adult Male 67.828 23353597 54.0 Adult Male null 23353599 75.0 Elderly Male null 23353600 56.0 Adult Female null 23353602 93.0 Elderly Male null 23353605 84.0 Elderly Male 106 23353610 71.0 Elderly Male null 23353611 84.0 Elderly Female null 23353613 65.0 Adult Male null 23353614 80.0 Elderly Male null 23353615 43.0 Adult Male null 23353616 46.0 Adult Male null 23353617 32.0 Adult Male null 23353618 53.0 Adult Male null 23353619 45.0 Adult Female null 23353620 43.0 Adult Female null 23353621 45.0 Adult Female null 23353623 59.0 Adult Female 69.4 23353626 24.0 Adult Male 87.5 23353627 79.0 Elderly Female null 23353629 39.0 Adult Male 107.94 23353630 47.0 Adult Female 99.7 23353631 47.0 Adult Female null 23353634 75.0 Elderly Female null 23353635 63.0 Adult Female null 23353637 40.0 Adult Female null 23353639 58.0 Adult Female null 23353640 55.0 Adult Female null 23353641 63.0 Adult Female 63 23353643 51.0 Adult Female null 23353644 70.0 Elderly Female 46 23353645 23.0 Adult Male null 23353646 56.0 Adult Male null 23353647 32.0 Adult Male null 23353649 61.0 Adult Male null 23353654 66.0 Elderly Male 62.14 23353662 76.0 Elderly Female null 23353663 62.0 Adult Female null 23353664 55.0 Adult Male null 23353670 50.0 Adult Male null 23353671 70.0 Elderly Female 145 23353676 69.0 Elderly Male 90.72 23353677 71.0 Elderly Male null 23353681 39.0 Adult Male null 23353685 74.0 Elderly Male null 23353688 52.0 Adult Male 68.95 23353689 40.0 Adult Female null 23353691 54.0 Adult Male null 23353696 65.0 Adult Female 67.5 23353697 43.0 Adult Female 78 23353698 59.0 Adult Male null 23353702 63.0 Adult Female null 23353710 73.0 Elderly Female 58.503 23353713 63.0 Adult Male 84.807 23353714 80.0 Elderly Female 66.68 23353716 51.0 Adult Female null 23353718 76.0 Elderly Female 68.027 23353724 59.0 Adult Female 59 23353725 54.0 Adult Female null 23353726 59.0 Adult Female 72.57 23353727 75.0 Elderly Male 83.91 23353728 66.0 Elderly Female 79.365 23353729 51.0 Adult Male 72.562 23353730 68.0 Elderly Female 67.12 23353733 39.0 Adult Male null 23353744 50.0 Adult Male 170.1 23353745 69.0 Elderly Female null 23353746 59.0 Adult Male null 23353748 43.0 Adult Male null 23353749 49.0 Adult Female null 23353750 42.0 Adult Female null 23353755 44.0 Adult Unknown null 23353761 60.0 Adult Female 79.38 23353762 23.0 Adult Female 54.43 23353764 40.0 Adult Unknown null 23353767 23.0 Adult Male null 23353769 80.0 Elderly Female null 23353770 39.0 Adult Female 48.073 23353772 24.0 Adult Female null 23353777 32.0 Adult Female null 23353780 75.0 Elderly Male null 23353782 49.0 Adult Female 67.12 23353790 17.0 Adolescent Female null 23353792 62.0 Adult Female 92.99 23353794 61.0 Adult Male null 23353796 41.0 Adult Female null 23353798 42.0 Adult Male null 23353802 84.0 Elderly Female 79.365 23353807 66.0 Elderly Male null 23353812 52.0 Adult Male 86.18 23353814 79.0 Elderly Female null 23353817 46.0 Adult Male null 23353819 46.0 Adult Female null 23353820 44.0 Adult Female null 23353822 74.0 Elderly Male null 23353824 3.0 Child Female null 23353825 13.0 Adolescent Female null 23353827 54.0 Adult Female null 23353829 38.0 Adult Male 85 23353830 43.0 Adult Male null 23353831 44.0 Adult Female null 23353832 95.0 Elderly Male null 23353834 10.0 Child Male null 23353835 50.0 Adult Female null 23353836 62.0 Adult Female 72 23353837 44.0 Adult Female 43.99 23353838 72.0 Elderly Male null 23353839 23.0 Adult Male null 23353840 93.0 Elderly Female 50.8 23353842 63.0 Adult Male 118 23353845 65.0 Adult Male null 23353846 57.0 Adult Female 84.5 23353847 66.0 Elderly Female null 23

In [0]:
dim_patient.printSchema()

root
 |-- patient_id: string (nullable = true)
 |-- patient_onset_age: double (nullable = true)
 |-- patient_age_group: string (nullable = true)
 |-- patient_sex: string (nullable = false)
 |-- patient_weight(kg): string (nullable = true)



##Parse Drug Information into Spark DataFrame for Drug Information dimension table

In [0]:
# Select key fields for viewing
dim_drug_information = exploded_df.select(
    col("results.safetyreportid").alias("safety_report_id"),
    col("results.patient.drug.medicinalproduct").alias("medicinal_product"),
    col("results.patient.drug.activesubstance.activesubstancename").alias("active_substance"),
    col("results.patient.drug.drugindication").alias("indication"),
    col("results.patient.drug.drugadministrationroute").alias("administration_route"),
    col("results.patient.drug.drugdosageform").alias("dosage_form"),
    col("results.patient.drug.openfda.pharm_class_pe").alias("pharmacodynamic_effect"),
    col("results.patient.drug.openfda.pharm_class_cs").alias("chemical_structure_class"),
    col("results.patient.drug.openfda.pharm_class_epc").alias("established_pharmacologic_class"),
    col("results.patient.drug.openfda.pharm_class_moa").alias("mechanism_of_action")
)

dim_drug_information= (dim_drug_information  
    .withColumn("tmp", arrays_zip("medicinal_product",
                                  "indication", 
                                  "administration_route", 
                                  "dosage_form"))
    .withColumn("tmp", explode_outer("tmp"))
    .select(col("tmp.medicinal_product"),
            col("tmp.indication"),
            col("tmp.administration_route"), 
            col("tmp.dosage_form")
    )
    .dropDuplicates(["medicinal_product"]))

# List of columns to convert to lowercase
cols_to_lower = ["medicinal_product", "indication", "dosage_form"]

for column_name in cols_to_lower:
    dim_drug_information = dim_drug_information.withColumn(column_name, lower(col(column_name)))


dim_drug_information = dim_drug_information.withColumn('indication', regexp_replace("indication", "\^", ""))

dim_drug_information = dim_drug_information.withColumn('medicinal_product', trim(regexp_replace("medicinal_product", "[\\(\\):\\[\\-+_\\^\\.?#*;,%\\d]", "")))
dim_drug_information = dim_drug_information.dropna(thresh=2)

dim_drug_information = dim_drug_information.withColumn('medicinal_product', regexp_replace("medicinal_product", "aluminium", "aluminum"))
dim_drug_information = dim_drug_information.withColumn("string_split", split(dim_drug_information["medicinal_product"], "\\\\"))
dim_drug_information = dim_drug_information.withColumn("medicinal_product", lower(dim_drug_information["string_split"].getItem(0)))
dim_drug_information = dim_drug_information.drop('string_split')


dim_drug_information = dim_drug_information.withColumn("string_split", split(dim_drug_information["medicinal_product"], "/"))
dim_drug_information = dim_drug_information.withColumn("medicinal_product", lower(trim(dim_drug_information["string_split"].getItem(0))))
dim_drug_information = dim_drug_information.drop('string_split')


dim_drug_information = dim_drug_information.withColumn(
    "medicinal_product",
    trim(substring(
        dim_drug_information["medicinal_product"],
        1,
        instr(dim_drug_information["medicinal_product"], " ") - 1
    )
))
dim_drug_information = dim_drug_information.filter(length(dim_drug_information.medicinal_product) >= 5)
dim_drug_information = dim_drug_information.filter(length(dim_drug_information.medicinal_product) < 20)
dim_drug_information = dim_drug_information.dropDuplicates(['medicinal_product'])


display(dim_drug_information)

medicinal_product indication administration_route dosage_form abacavir product used for unknown indication 065 null abasaglar null null solution for injection in pre-filled pen abemaciclib neoplasm malignant 048 null abilify schizophrenia 065 suspension for injection abiraterone prostate cancer 048 null abreva product used for unknown indication null null absorbine product used for unknown indication 061 null absorica product used for unknown indication 065 capsule acamprosate null null tablet acarbose diabetes mellitus 048 tablet, orally disintegrating accord asthma null null accorduk product used for unknown indication null null acebutolol hypertension 065 tablet acepromazine product used for unknown indication 065 null acetal body temperature increased 048 tablet acetamin product used for unknown indication null null acetaminophe product used for unknown indication null null acetaminophen product used for unknown indication 065 unknown acetaminophene product used for unknown indication null null acetaminophn product used for unknown indication 065 suspension acetate infection prophylaxis 003 null acetazolamide product used for unknown indication 065 null acetic product used for unknown indication 065 unknown acetonide product used for unknown indication null null acetphen adverse event 042 null acetyl product used for unknown indication 065 null acetylcholine product used for unknown indication 065 null acetylcystein null 048 effervescent tablet acetylcysteine productive cough 055 null acetylcysteinefolic product used for unknown indication 048 null acetylleucine product used for unknown indication 065 null acetylsalicalic cerebrovascular accident 048 null acetylsalicylic product used for unknown indication 065 null acetylsalylicylic product used for unknown indication 048 null achillea product used for unknown indication 065 null achromycin pityriasis rubra pilaris 048 capsule aciclovir product used for unknown indication null null acide drug toxicity prophylaxis 048 tablet acidex dyspepsia null null acido product used for unknown indication 065 null acidophilus product used for unknown indication null null acidum cardiovascular event prophylaxis 065 null aciklovir null 048 tablet aciloc product used for unknown indication null null acitretin psoriasis 065 null acivir null null tablet aclarubicin acute myeloid leukaemia 041 powder for solution for injection aclidinium null 065 null aclova product used for unknown indication 065 null aconitum hypertension null null acotiamide abdominal distension 048 tablet acovil product used for unknown indication null null acrosar hypertension 065 null actaea menopause 048 null actavis product used for unknown indication 048 tablet actemra rheumatoid arthritis 058 null actifed product used for unknown indication 065 null actinomycin malignant hydatidiform mole 065 null actiskenan product used for unknown indication null null actisorb product used for unknown indication 065 dental gel activated acute kidney injury 065 unknown actonel osteoporosis postmenopausal 048 film-coated tablet actoplus product used for unknown indication 048 unknown actraphane diabetes mellitus 058 null actrapid product used for unknown indication null solution for injection in pre-filled syringe acupan product used for unknown indication null null acuvue product used for unknown indication 065 ophthalmic insert acyclo antiviral prophylaxis 065 null acyclovir infection prophylaxis null null acylovir product used for unknown indication null tablet acyrax null 048 null adacel product used for unknown indication null injection adalat null null prolonged-release tablet adalimumab null 065 null adamon pneumothorax null null adamts product used for unknown indication 065 unk adapalene product used for unknown indication null null adcosimvastatin blood cholesterol null null adderall product used for unknown indication 065 unk adefovir hepatic cirrhosis 048 tablet ademetionine null null injection adenosine acute myeloid le

##Parse Report Metadata into Spark DataFrame

In [0]:
# Select key fields for viewing
dim_report_metadata = exploded_df.select(
    col("results.safetyreportid").alias("safety_report_id"),
    col("results.occurcountry").alias("occurance_country"),
    to_date(col("results.receivedate"), "yyyyMMdd").alias("date_report_received"),
    to_date(col("results.transmissiondate"), "yyyyMMdd").alias("date_of_transmission"),
    col("results.companynumb").alias("reported_company")
)

# Split the string by dashes
dim_report_metadata = dim_report_metadata.withColumn("string_split", split(dim_report_metadata["reported_company"], "-"))

# Extract the string between the first and second dashes
dim_report_metadata = dim_report_metadata.withColumn("reported_company", lower(dim_report_metadata["string_split"].getItem(1)))
dim_report_metadata = dim_report_metadata.withColumn('reported_company', trim(regexp_replace("reported_company", "inc", "")))
dim_report_metadata = dim_report_metadata.withColumn('reported_company', trim(regexp_replace("reported_company", "[,]", "")))
dim_report_metadata = dim_report_metadata.withColumn('reported_company', regexp_replace("reported_company", "[._]", " "))


dim_report_metadata = dim_report_metadata.drop('string_split')
# Show the flattened data
display(dim_report_metadata)

safety_report_id occurance_country date_report_received date_of_transmission reported_company 23353582 US 2024-01-01 2024-04-10 sa 23353583 US 2024-01-01 2024-04-10 amgen 23353584 US 2024-01-01 2024-04-10 amgen 23353585 CA 2024-01-01 2024-04-10 abbvie 23353586 US 2024-01-01 2024-04-09 amgen 23353587 US 2024-01-01 2024-04-09 abbvie 23353588 CA 2024-01-01 2024-04-10 abbvie 23353589 CN 2024-01-01 2024-04-10 abbvie 23353590 CA 2024-01-01 2024-04-09 abbvie 23353591 CA 2024-01-01 2024-04-09 abbvie 23353592 CA 2024-01-01 2024-04-10 abbvie 23353593 CA 2024-01-01 2024-04-10 amgen 23353594 CA 2024-01-01 2024-04-09 aurobindo 23353595 CO 2024-01-01 2024-04-10 abbvie 23353596 null 2024-01-01 2024-04-10 roche 23353597 FR 2024-01-01 2024-04-09 afssaps 23353598 US 2024-01-01 2024-04-10 abbvie 23353599 IE 2024-01-01 2024-04-09 abbvie 23353600 null 2024-01-01 2024-04-09 roche 23353601 IT 2024-01-01 2024-04-10 jnjfoc 23353602 IL 2024-01-01 2024-04-09 abbvie 23353603 US 2024-01-01 2024-04-10 abbvie 23353604 null 2024-01-01 2024-04-10 null 23353605 null 2024-01-01 2024-04-10 null 23353606 US 2024-01-01 2024-04-10 sa 23353607 US 2024-01-01 2024-04-10 abbvie 23353608 null 2024-01-01 2024-04-09 null 23353609 null 2024-01-01 2024-04-09 null 23353610 US 2024-01-01 2024-04-10 amgen 23353611 US 2024-01-01 2024-04-10 amgen 23353612 AU 2024-01-01 2024-04-09 abbvie 23353613 FR 2024-01-01 2024-04-10 abbvie 23353614 CO 2024-01-01 2024-04-10 abbvie 23353615 US 2024-01-01 2024-04-10 sa 23353616 US 2024-01-01 2024-04-10 sa 23353617 US 2024-01-01 2024-04-09 sa 23353618 null 2024-01-01 2024-04-10 roche 23353619 null 2024-01-01 2024-04-09 roche 23353620 IT 2024-01-01 2024-04-10 null 23353621 US 2024-01-01 2024-07-16 sa 23353623 null 2024-01-01 2024-04-10 null 23353625 US 2024-01-01 2024-04-10 sanofi 23353626 US 2024-01-01 2024-04-10 sa 23353627 US 2024-01-01 2024-04-10 amgen 23353628 US 2024-01-01 2024-04-10 amgen 23353629 US 2024-01-01 2024-04-09 amgen 23353630 US 2024-01-01 2024-04-10 amgen 23353631 US 2024-01-01 2024-07-16 amgen 23353632 JP 2024-01-01 2024-04-09 dsjp 23353633 AR 2024-01-01 2024-04-10 abbvie 23353634 US 2024-01-01 2024-04-09 amgen 23353635 US 2024-01-01 2024-04-10 amgen 23353636 AR 2024-01-01 2024-04-10 abbvie 23353637 US 2024-01-01 2024-04-10 sa 23353638 US 2024-01-01 2024-04-10 sa 23353639 US 2024-01-01 2024-04-10 sa 23353640 US 2024-01-01 2024-04-10 sa 23353641 US 2024-01-01 2024-04-10 sa 23353642 US 2024-01-01 2024-04-10 sa 23353643 US 2024-01-01 2024-04-10 sa 23353644 CN 2024-01-01 2024-04-10 sa 23353645 US 2024-01-01 2024-04-10 sa 23353646 US 2024-01-01 2024-04-09 sa 23353647 US 2024-01-01 2024-04-10 viiv healthcare limited 23353648 US 2024-01-01 2024-04-10 purdue 23353649 US 2024-01-01 2024-04-10 purdue 23353650 US 2024-01-01 2024-04-10 purdue 23353651 US 2024-01-01 2024-04-10 purdue pharma 23353652 US 2024-01-01 2024-04-10 purdue pharma 23353653 US 2024-01-01 2024-04-10 purdue pharma 23353654 US 2024-01-01 2024-04-10 purdue pharma 23353655 US 2024-01-01 2024-04-10 purdue pharma 23353656 US 2024-01-01 2024-04-10 purdue pharma 23353657 US 2024-01-01 2024-04-09 purdue pharma 23353658 US 2024-01-01 2024-04-09 purdue pharma 23353659 US 2024-01-01 2024-04-10 purdue pharma 23353660 US 2024-01-01 2024-04-10 purdue pharma 23353661 US 2024-01-01 2024-04-09 purdue pharma 23353662 US 2024-01-01 2024-04-09 purdue pharma 23353663 US 2024-01-01 2024-04-10 purdue pharma 23353664 US 2024-01-01 2024-04-09 purdue pharma 23353665 US 2024-01-01 2024-04-10 purdue 23353666 US 2024-01-01 2024-04-09 purdue pharma 23353667 US 2024-01-01 2024-04-09 purdue pharma 23353668 US 2024-01-01 2024-04-09 purdue pharma 23353669 US 2024-01-01 2024-04-10 purdue pharma 23353670 MY 2024-01-01 2024-04-10 abbvie 23353671 US 2024-01-01 2024-04-10 purdue pharma 23353672 US 2024-01-01 2024-04-09 purdue pharma 23353673 US 2024-01-01 2024-04-09 purdue pharma 23353674 US 2024-01-01 2024-04-10 purdue pharma 23353675 US 2024-01-01 2024-04-10 purdue pharma 23353676 US 2024-01-01 2024-04-10

##Parse Reaction Data into Spark DataFrame

In [0]:
# Select key fields for viewing
fact_reaction = exploded_df.select(
    col("results.safetyreportid").alias("patient_id"),
    col("results.patient.reaction.reactionmeddrapt").alias("patient_reaction"),
    col("results.patient.reaction.reactionoutcome").alias("reaction_outcome"),
    col("results.patient.drug.actiondrug").getItem(0).alias("action_taken"),
    col("results.patient.drug.medicinalproduct").getItem(0).alias("medicinal_product"),
    col("results.seriousnessdeath").alias("patient_death"),
    col("results.seriousnesslifethreatening").alias("life_threatening"),
    col("results.seriousnessdisabling").alias("disabling"),
    col("results.seriousnesshospitalization").alias("hospitalization"),
    col("results.seriousnesscongenitalanomali").alias("congenital_anomaly"),
    col("results.seriousnessother").alias("other_issues"),
    col("results.patient.drug.drugstartdate").alias("start_dosage_date"),
    col("results.patient.drug.drugenddate").alias("end_dosage_date"),

)

fact_reaction = fact_reaction.withColumn("reaction_severity", 
                                         when(fact_reaction.patient_death == "1", 1)
                                         .when(fact_reaction.life_threatening == "1", 2)
                                         .when(fact_reaction.disabling == "1", 3)
                                         .when(fact_reaction.hospitalization == "1", 4)
                                         .when(fact_reaction.congenital_anomaly == "1", 5)
                                         .when(fact_reaction.other_issues == "1", 6)
                                         .otherwise(7))

fact_reaction= (fact_reaction  
    .withColumn("tmp", arrays_zip("patient_reaction",
                                  "reaction_outcome",
                                  "start_dosage_date", 
                                  "end_dosage_date"))
    .withColumn("tmp", explode("tmp"))
    .select(col("patient_id"),
            col("tmp.patient_reaction"), 
            col("tmp.reaction_outcome"),
            col("reaction_severity"),
            col("action_taken"),
            col("medicinal_product"),
            to_date(col("tmp.start_dosage_date"),'yyyyMMdd').alias("dosage_start_date"), 
            to_date(col("tmp.end_dosage_date"), 'yyyyMMdd').alias("dosage_end_date"))
    .distinct()
    .dropna(subset=['patient_reaction']))


# List of columns to convert to lowercase
cols_to_lower = ["patient_reaction", "medicinal_product"]

for column_name in cols_to_lower:
    fact_reaction = fact_reaction.withColumn(column_name, lower(col(column_name)))

fact_reaction = fact_reaction.drop('patient_death', 'life_threatening', 'disabling', 'hospitalization', 'congenital_anomaly', 'other_issues')

# Step 1: Define the window specification
window_spec = Window.partitionBy("patient_id")

# Step 2: Get the max dosage_start_date within each safety_report_id group
df_with_max_date = fact_reaction.withColumn(
    "max_dosage_start_date", max(col("dosage_start_date")).over(window_spec)
).withColumn(
    "max_dosage_end_date", max(col("dosage_end_date")).over(window_spec)
)

# Step 3: Use coalesce to replace NULL dosage_start_date with the non-null value from max_dosage_start_date
df_filled = df_with_max_date.withColumn("start_dosage_date", coalesce("dosage_start_date", "max_dosage_start_date")).withColumn("end_dosage_date", coalesce("dosage_end_date", "max_dosage_end_date"))

# Step 4: Drop the extra max_dosage_start_date column if no longer needed
fact_reaction = df_filled.drop("max_dosage_start_date", "max_dosage_end_date", "dosage_start_date", "dosage_end_date")

fact_reaction = fact_reaction.withColumn('medicinal_product', trim(regexp_replace("medicinal_product", "[\\(\\):\\[\\-+_\\^\\.?#*;,%\\d]", "")))
fact_reaction = fact_reaction.dropna(thresh=2)

fact_reaction = fact_reaction.withColumn('medicinal_product', regexp_replace("medicinal_product", "aluminium", "aluminum"))
fact_reaction = fact_reaction.withColumn("string_split", split(fact_reaction["medicinal_product"], "\\\\"))
fact_reaction = fact_reaction.withColumn("medicinal_product", lower(fact_reaction["string_split"].getItem(0)))
fact_reaction = fact_reaction.drop('string_split')

fact_reaction = fact_reaction.withColumn("string_split", split(fact_reaction["medicinal_product"], "/"))
fact_reaction = fact_reaction.withColumn("medicinal_product", lower(trim(fact_reaction["string_split"].getItem(0))))
fact_reaction = fact_reaction.drop('string_split')

fact_reaction = fact_reaction.withColumn(
    "medicinal_product",
    substring(
        fact_reaction["medicinal_product"],
        1,
        instr(fact_reaction["medicinal_product"], " ") - 1
    )
)
fact_reaction = fact_reaction.filter(length(fact_reaction.medicinal_product) >= 5)
fact_reaction = fact_reaction.filter(length(fact_reaction.medicinal_product) < 20)


display(fact_reaction)

patient_id patient_reaction reaction_outcome reaction_severity action_taken medicinal_product start_dosage_date end_dosage_date 23353698 death 5 1 6 leuprolide null null 23353707 nausea 6 7 1 aptensio null null 23353707 dry mouth 6 7 1 aptensio null null 23353741 product formulation issue 3 7 4 oxycodone null null 23353741 drug ineffective 3 7 4 oxycodone null null 23353750 drug diversion 6 7 5 oxycodone null null 23353754 product physical issue 6 7 5 dextroamphet null null 23353754 drug ineffective 6 7 5 dextroamphet null null 23353755 drug diversion 6 7 5 oxycodone null null 23353756 drug diversion 6 7 5 oxycodone null null 23353760 drug effect less than expected 6 7 5 oxycodone null null 23353778 drug ineffective 6 7 5 oxycodone null null 23353778 product quality issue 6 7 5 oxycodone null null 23353778 balance disorder 6 7 5 oxycodone null null 23353787 drug ineffective 6 7 3 oxycodone null null 23353787 product size issue 6 7 3 oxycodone null null 23353791 constipation 3 7 5 oxycodone null null 23353791 product use in unapproved indication 6 7 5 oxycodone null null 23353792 product colour issue 6 7 1 oxycodone 2023-11-12 2023-11-13 23353792 drug interaction 6 7 1 oxycodone 2023-11-12 2023-11-13 23353792 pruritus 6 7 1 oxycodone 2023-11-12 2023-11-13 23353801 malaise 6 7 5 oxycodone null null 23353801 abdominal pain upper 6 7 5 oxycodone null null 23353801 headache 6 7 5 oxycodone null null 23353801 nausea 6 7 5 oxycodone null null 23353801 product use complaint 6 7 5 oxycodone null null 23353801 product size issue 6 7 5 oxycodone null null 23353801 balance disorder 6 7 5 oxycodone null null 23353801 dizziness 6 7 5 oxycodone null null 23353801 drug ineffective 6 7 5 oxycodone null null 23353883 unresponsive to stimuli 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 rales 2 4 1 zolpidem 2023-12-16 2023-12-17 23353883 disorganised speech 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 delirium 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 infection 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 tremor 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 chest discomfort 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 mania 2 4 1 zolpidem 2023-12-13 2023-12-19 23353883 hypoaesthesia 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 hyperventilation 6 4 1 zolpidem 2023-12-11 2023-12-12 23353883 tachypnoea 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 amnesia 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 mental disorder 2 4 1 zolpidem 2023-12-16 2023-12-20 23353883 hyperlactacidaemia 6 4 1 zolpidem 2023-12-16 2023-12-16 23353965 hypervolaemia 1 4 1 delflex null null 23353965 hypertension 1 4 1 delflex null null 23353989 gastrointestinal inflammation 1 4 5 mycophenolate null null 23353989 diverticulum intestinal 6 4 5 mycophenolate null null 23353989 diverticulitis 1 4 5 mycophenolate null null 23353989 epiploic appendagitis 1 4 5 mycophenolate null null 23353989 colitis 1 4 5 mycophenolate null null 23353989 gastrointestinal infection 6 4 5 mycophenolate null null 23354024 hypophagia 2 4 5 mycophenolate null null 23354024 weight decreased 2 4 5 mycophenolate null null 23354024 diarrhoea 2 4 5 mycophenolate null null 23354024 toxicity to various agents 2 4 5 mycophenolate null null 23354024 vomiting 2 4 5 mycophenolate null null 23354024 acute kidney injury 2 4 5 mycophenolate null null 23354024 asthenia 2 4 5 mycophenolate null null 23354215 inappropriate schedule of product administration 6 7 6 xyzal 2023-12-20 null 23354285 dyspnoea 2 4 4 valacyclovir 2023-08-07 2023-10-02 23354285 diarrhoea 2 4 4 valacyclovir 2023-07-10 2023-10-02 23354285 vomiting 1 4 4 valacyclovir 2023-08-07 2023-10-02 23354285 asthenia 2 4 4 valacyclovir 2023-08-07 2023-10-02 23354320 blood potassium decreased 1 4 4 dianeal null null 23354320 oxygen saturation decreased 1 4 4 dianeal null null 23354342 haematoma 4 2 1 enoxaparin 2023-10-05 2023-11-29 23354342 status epilepticus 1 2 1 enoxaparin 2023-10-05 2023-11-29 23354355 in vitro fertilisation 6 7 4 agalsidase 2014-0

In [0]:
fact_reaction.printSchema()

root
 |-- patient_id: string (nullable = true)
 |-- patient_reaction: string (nullable = true)
 |-- reaction_outcome: string (nullable = true)
 |-- reaction_severity: integer (nullable = false)
 |-- action_taken: string (nullable = true)
 |-- medicinal_product: string (nullable = true)
 |-- start_dosage_date: date (nullable = true)
 |-- end_dosage_date: date (nullable = true)



In [0]:
print(latest_file)
year = (latest_file.split("_")[4]).split('.')[0].split('-')[0]
print(year)

dbfs:/mnt/adverse-events/raw-data/fda_adverse_events_extract_2024-01-01-TO-2024-12-31.json
2024


In [0]:

fact_reaction.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/transformed-data/fact_reaction_{year}.csv")
dim_patient.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/transformed-data/dim_patient_{year}.csv")
dim_drug_information.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/transformed-data/dim_drug_information_{year}.csv")
dim_report_metadata.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/transformed-data/dim_report_metadata_{year}.csv")